# Exploration


In [11]:
import pandas as pd

# Read the data

df = pd.read_csv("data/Opportunites.csv", sep=";", encoding="ISO-8859-1")

# drop 7 last rows

df = df[:-7]

# Strategy


- Que faire des doubles dans la colonne N° Opportunité ?
- Pourquoi y a-t-il toujours une date de cloture ? Est-ce une date estimée ?
- Dans la colonne 'Nom du compte', il y a en champ 'DOUBLON NE PAS UTILISER'. Est-ce une indication pour moi ?
- Ai-je le droit d'utiliser les informations sur les employés dans l'algorithme ? Les noms et prénoms des clients ?

- Comment catégoriser 'Étape' ?
  0- Etude amont / Budget 2430
  1- Priorisation 27
  2- Dépôt de candidature 30
  3- Réponse en préparation 1316
  4- Réponse envoyée 8565
  5- Négociation prix 286
  6- Gagnée 19978
  7- Perdue 21379
  8- Perdue archivée 8226
  9- Gagnée archivée 1620


Plan:

- Drop 'N° Opportunité' (clef)
- Drop 'Nom de l'opportunité' (clef, analyse plus tard?)
- Drop 'Date de clôture' (information tirée du futur)
- Drop 'Date de création' et 'Date de dernière modification'
- Drop 'Date de démarrage estimé de l'affaire' (58161 Nan over 63864)
- Drop 'Durée estimée du chantier (nb mois)' (61167 Nan over 63864)
- Convert 'Montant' to float
- Drop rows where 'Montant' is Nan
- Drop 'Probabilité (%)'
- Drop 'Nom du compte' (Texte complexe)
- Drop 'Activité' (56 valeurs différentes)
- Drop 'Resp.' (135 employés différents) et 'Resp..1' (136 valeurs ?)
- Drop 'Prénom' and 'Nom'
- Drop 'Rôle du contact' (18 valeurs différentes, moitié de Nan)
- Drop 'Motif si perdue' (information tirée du futur)
- One hot 'Origine de l'opportunité' (8 valeurs différentes)
- Drop 'Locaux' (32 valeurs différentes)
- One hot 'Opération' (2 valeurs)
- One hot 'Domaine' (2 valeurs)
- One hot 'Position' (2 valeurs)
- One hot 'Type du compte' (6 valeurs dont 442 Nan)
- A voir pour 'Étape'
- Drop 'Ville' (7142 villes différentes)

Futur:

- Travailler sur 'Nom du compte' ("Ville, entreprise, taille de l'entreprise, etc)
- Travailler sur 'Activité'
- Travailler sur 'Resp.' et 'Resp..1' (lier la table staff)
- One hot 'Rôle du contact'
- Travailler sur 'Locaux'
- Travailler sur 'Ville' (Ajouter des données géographiques, densité, prix au m^2, population, etc.)


In [3]:
def unique_values(df, column):
    return df[column].unique()


def count_values(df, column):
    return df[column].value_counts()


def count_nan(df, column):
    return df[column].isna().sum()

In [19]:
print(df.shape)
print(df.columns)
# df.head()

(63857, 25)
Index(['N° Opportunité', 'Nom de l'opportunité', 'Date de clôture',
       'Date de création', 'Date de dernière modification',
       'Date de démarrage estimé de l'affaire',
       'Durée estimée du chantier (nb mois)', 'Montant', 'Probabilité (%)',
       'Nom du compte', 'Activité', 'Resp.', 'Prénom', 'Nom',
       'Rôle du contact', 'Motif si perdue', 'Origine de l'opportunité',
       'Locaux', 'Opération', 'Domaine', 'Position', 'Resp..1',
       'Type du compte', 'Étape', 'Ville'],
      dtype='object')


In [4]:
col = "Étape"

unique = unique_values(df, col)
values_count = count_values(df, col)

print(unique.shape)
print(unique)
print(values_count)
print(count_nan(df, col))

(10,)
['4- Réponse envoyée' '7- Perdue' '8- Perdue archivée' '6- Gagnée'
 '9- Gagnée archivée' '0- Etude amont / Budget'
 '3- Réponse en préparation' '5- Négociation prix' '1- Priorisation'
 '2- Dépôt de candidature']
Étape
6- Gagnée                    19897
7- Perdue                    19683
4- Réponse envoyée            8405
8- Perdue archivée            7216
0- Etude amont / Budget       1737
9- Gagnée archivée            1611
5- Négociation prix            286
3- Réponse en préparation      213
1- Priorisation                 15
2- Dépôt de candidature         12
Name: count, dtype: int64
0


# Processing


In [1]:
import pandas as pd


def to_one_hot(data: pd.DataFrame, columns: list) -> pd.DataFrame:
    """
    Convert the given columns to one hot encoding
    The original columns are dropped and the new ones should be named according to the category they represent

    :param data: The data to convert
    :param columns: The columns to convert

    :return: The converted data
    """
    for column in columns:
        one_hot = pd.get_dummies(data[column], prefix=column)
        data = data.drop(column, axis=1)
        data = data.join(one_hot)
    return data


def to_binary_one_hot(data: pd.DataFrame, columns: list) -> pd.DataFrame:
    """
    Convert the given column to one hot encoding
    The original column is dropped and the new ones should be named according to the category they represent

    :param data: The data to convert
    :param column: The column to convert

    :return: The converted data
    """
    for column in columns:
        one_hot = pd.get_dummies(data[column], prefix=column)
        data = data.drop(column, axis=1)

        positive_value = one_hot.columns[0]
        data[f"{column}_{positive_value}"] = one_hot[positive_value]

    return data


def load_opportunities() -> pd.DataFrame:
    df = pd.read_csv("data/Opportunites.csv", sep=";", encoding="ISO-8859-1")
    df = df[:-7]

    keep_cols = [
        "Montant",
        "Origine de l'opportunité",
        "Opération",
        "Domaine",
        "Position",
        "Type du compte",
        "Étape",
        "Date de dernière modification",
    ]

    binary_one_hot_cols = ["Opération", "Domaine", "Position"]

    one_hot_cols = [
        "Origine de l'opportunité",
        "Type du compte",
    ]

    df = df[keep_cols]

    # 'Montant' to float

    df["Montant"] = df["Montant"].str.replace(",", ".").astype(float)

    # To one hot

    df = to_binary_one_hot(df, binary_one_hot_cols)

    df = to_one_hot(df, one_hot_cols)

    # Drop NaN in 'Montant'

    df = df.dropna(subset=["Montant"])

    # Drop negative values in 'Montant'

    df = df[df["Montant"] > 0]

    df["Label"] = None

    # if 'Étape' in ['6- Gagnée', '9- Gagnée archivée'] then 'Label' = 1
    # If 'Étape' in ['7- Perdue', '8- Perdue archivée'] then 'Label' = 0

    df.loc[df["Étape"].isin(["6- Gagnée", "9- Gagnée archivée"]), "Label"] = 1
    df.loc[df["Étape"].isin(["7- Perdue", "8- Perdue archivée"]), "Label"] = 0

    df["jours depuis dernière modification"] = (
        pd.to_datetime("today")
        - pd.to_datetime(df["Date de dernière modification"], format="%d/%m/%Y")
    ).dt.days

    # if 'Label' is NaN and 'jours depuis dernière modification' > 2*365 then 'Label' = 0
    df.loc[
        (df["Label"].isna()) & (df["jours depuis dernière modification"] > 2 * 365),
        "Label",
    ] = 0

    # Drop NaN in 'Label'

    df = df.dropna(subset=["Label"])

    # Drop 'Étape', 'Date de dernière modification' and 'jours depuis dernière modification'

    df = df.drop(
        [
            "Étape",
            "Date de dernière modification",
            "jours depuis dernière modification",
        ],
        axis=1,
    )

    return df

# Visualization


In [14]:
# Plot PCA of data with labels on plotly
import pandas as pd
import numpy as np
from scipy import stats

df = load_opportunities()
labels = df["Label"]
df = df.drop("Label", axis=1)

filter_mask = np.abs(stats.zscore(df["Montant"])) < 3
df = df[filter_mask]
labels = labels[filter_mask]

# Normalize data

from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()

normalized_df = scaler.fit_transform(df)

from sklearn.decomposition import PCA

pca = PCA(n_components=2)

pca.fit(normalized_df)

df_pca = pca.transform(normalized_df)

import plotly.express as px

fig = px.scatter(
    x=df_pca[:, 0],
    y=df_pca[:, 1],
    color=labels,
    color_continuous_scale=px.colors.sequential.Viridis,
)

fig.show()

In [15]:
# print PCA vectors

print(pca.components_)
print(pca.explained_variance_ratio_)

print(df.columns)

[[ 0.08406883 -0.37758787 -0.04083861  0.44119215  0.07911743  0.27167214
  -0.00080015 -0.335504    0.0926556   0.05427986  0.08882525  0.00335619
  -0.47983971  0.00256573  0.05564902  0.45650663  0.01523919]
 [-0.26738839  0.0855204   0.35098326  0.01109356 -0.01167577 -0.29437167
   0.02031563 -0.36232348  0.61744027  0.0959728   0.18033227  0.01475926
  -0.001143    0.04568845  0.34023797 -0.16668329  0.10286208]]
[0.21305346 0.08582534]
Index(['Montant', 'Opération_Opération_NF', 'Domaine_Domaine_BT',
       'Position_Position_DR', 'Origine de l'opportunité_Appel d'offre privé',
       'Origine de l'opportunité_Appel d'offre public',
       'Origine de l'opportunité_Chantier vu',
       'Origine de l'opportunité_Consultation directe ancien Client',
       'Origine de l'opportunité_Consultation directe nouveau Client',
       'Origine de l'opportunité_Conversation',
       'Origine de l'opportunité_Expertise', 'Origine de l'opportunité_SPPM',
       'Type du compte_Entreprise BTP'

In [2]:
# Plot TSNE of data with labels on plotly

import pandas as pd
import numpy as np
from scipy import stats

df = load_opportunities()
labels = df["Label"]
df = df.drop("Label", axis=1)

filter_mask = np.abs(stats.zscore(df["Montant"])) < 3
df = df[filter_mask]
labels = labels[filter_mask]

# Normalize data

# from sklearn.preprocessing import StandardScaler

# scaler = StandardScaler()

# normalized_df = scaler.fit_transform(df)

from sklearn.manifold import TSNE


tsne = TSNE(n_components=2)

df_tsne = tsne.fit_transform(df)

import plotly.express as px

fig = px.scatter(
    x=df_tsne[:, 0],
    y=df_tsne[:, 1],
    color=labels,
    color_continuous_scale=px.colors.sequential.Viridis,
)

fig.show()

In [38]:
# Plot correlation between labels and each feature

import pandas as pd
import numpy as np
from scipy import stats

df = load_opportunities()
labels = df["Label"]
df = df.drop("Label", axis=1)

filter_mask = np.abs(stats.zscore(df["Montant"])) < 3
df = df[filter_mask]
labels = labels[filter_mask]

# Plot correlation between labels and each feature

from sklearn.feature_selection import r_regression


correlations = r_regression(df.astype(float), labels.values.astype(float))

print(correlations)

import plotly.express as px

fig = px.bar(
    x=df.columns,
    y=correlations,
    color=correlations,
    color_continuous_scale=px.colors.sequential.Viridis,
)

fig.show()

[-0.04638921 -0.05189914  0.03434482  0.04846397 -0.00222875 -0.00867171
  0.0035939   0.00757615 -0.03596933  0.01871626  0.06298126  0.00068448
 -0.06081425 -0.00802313 -0.05500763  0.08967181 -0.00640394]


# Algorithm


In [2]:
# dataset import and split

import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split

df = load_opportunities()

labels = df["Label"].values.astype(bool)
features = df.drop("Label", axis=1).values


X_train, X_test, y_train, y_test = train_test_split(
    features, labels, test_size=0.2, random_state=42
)

In [11]:
# train logistic regression

from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score

clf = LogisticRegression(random_state=0).fit(X_train, y_train)

print(accuracy_score(y_train, clf.predict(X_train)))
print(accuracy_score(y_test, clf.predict(X_test)))

0.6138394872257832
0.6039541392073666


In [16]:
# train random forest

from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score


clf = RandomForestClassifier(max_depth=80, random_state=0).fit(X_train, y_train)


print(accuracy_score(y_train, clf.predict(X_train)))
print(accuracy_score(y_test, clf.predict(X_test)))

0.944502121513045
0.7329601877764738


In [ ]:
# train xgboost

import xgboost as xgb
from sklearn.metrics import accuracy_score

clf = xgb.XGBClassifier().fit(X_train, y_train)

print(accuracy_score(y_train, clf.predict(X_train)))

print(accuracy_score(y_test, clf.predict(X_test)))